In [25]:
import pandas as pd
from functions import custom_cv_eval_v2
import random
import json


In [26]:
%run MODEL_LIST.ipynb            #Load the models

In [27]:
df=pd.read_csv("data/owl-with-odds.csv")

In [28]:
#The odds need to be changed to numeric...

subset = ['t1_odds', 't2_odds']
df.dropna(subset=subset ,inplace=True)
df['t1_odds'] = pd.to_numeric(df['t1_odds'], errors='coerce')
df['t2_odds'] = pd.to_numeric(df['t2_odds'], errors='coerce')
df.dropna(subset=subset ,inplace=True)
#Create the odds df
odds_df = df[subset]

#Create a label df
label_df = df['winner_label']

In [29]:
#Split the test set.  We are always(?) going to use the last 60 matches as the test set, so we don't want those around
#as we pick models
df_train = df[:-60]
odds_train = odds_df[:-60]
label_train = label_df[:-60]

df_test = df[-60:]
odds_test = odds_df[-60:]
label_test = label_df[-60:]

print(len(df_test))
print(len(odds_test))
print(len(label_test))

print(len(df_train))
print(len(odds_train))
print(len(label_train))

60
60
60
508
508
508


In [30]:
model_1

LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
                   intercept_scaling=1, l1_ratio=None, max_iter=10000,
                   multi_class='auto', n_jobs=None, penalty='none',
                   random_state=75, solver='saga', tol=0.0001, verbose=0,
                   warm_start=False)

In [31]:
def get_ev(input_df, input_model, input_features, input_labels, odds_input):
    df_sel = input_df[input_features]
    df_sel = df_sel.dropna()
    labels_sel = input_labels[input_labels.index.isin(df_sel.index)]
    odds_sel = odds_input[odds_input.index.isin(df_sel.index)] 
    best_score = custom_cv_eval_v2(df_sel, input_model, labels_sel, odds_sel)
    return best_score

In [32]:
def tune_LogisticRegression(input_model, input_features, input_df, input_labels, odds_input):
    ###############################################################################################################
    #Parameters we are going to fine-tune:
    #1. penalty ('l1' or 'l2')
    #2. tol (original_value, original_value * 1.2, original_value * 0.8, rand(0, 10)
    #3. random_state = 75
    #4. solver = 'newton-cg', 'lbfgs', 'sag', 'saga'    
    ###############################################################################################################
    output_model = input_model
    best_score = -1000
    penalty = ['l1', 'l2', 'none']
    solver = ['newton-cg', 'lbfgs', 'sag', 'saga']
    tol = [input_model.tol, input_model.tol * 1.2, input_model.tol * .8, random.random() * 10 ]
    for s in solver:
        score = -10000
        for p in penalty:
            for t in tol:
                if ((s == 'newton-cg') & (p == 'l1')) |\
                ((s == 'lbfgs') & (p == 'l1')) |\
                ((s == 'sag') & (p == 'l1')):

                    pass
                else:
                    test_model = LogisticRegression(solver = s, penalty = p, tol=t, random_state=75, max_iter=10000)
                    score = get_ev(input_df, test_model, input_features, input_labels, odds_input)
                    if score > best_score:
                        best_score = score
                        output_model = test_model
                        print(p, s, t, best_score)
    return(output_model)

In [33]:
def tune_DecisionTreeClassifier(input_model, input_features, input_df, input_labels, odds_input):
    ###############################################################################################################
    #Parameters we are going to fine-tune:
    #1. criterion ('gini', 'entropy')
    #2. splitter ('random', 'best')
    #3. max_depth ('none', IF A NUMBER EXISTS +2, +4, -2, -4 ELSE 4 RANDOM INTS 1->100)
    #4. min_samples_leaf(n-1, n-2, 0,  n+1, n+2)
    #5. max_leaf_nodes:('none', n+1, n+2, n-1, n-2, OR 4 random numbers)
    ###############################################################################################################
    output_model = input_model
    best_score = -1000
    criterion = ['gini', 'entropy']
    splitter = ['random', 'best']
    if input_model.max_depth == None:
        max_depth = [None, random.randrange(100), random.randrange(100), random.randrange(100), random.randrange(100)]
    else:
        max_depth = [input_model.max_depth, input_model.max_depth - 2, input_model.max_depth - 1,  
                     input_model.max_depth + 1, input_model.max_depth + 2, random.randrange(100)]
        max_depth = [i for i in max_depth if i > 0]

    min_samples_leaf = [input_model.min_samples_leaf, input_model.min_samples_leaf - 2, input_model.min_samples_leaf - 1,
                         input_model.min_samples_leaf + 1, input_model.min_samples_leaf + 2, random.randrange(100)]
    min_samples_leaf = [i for i in min_samples_leaf if i > 0]    
    if input_model.max_leaf_nodes == None:
        max_leaf_nodes = [None, random.randrange(1000), random.randrange(1000), random.randrange(1000), random.randrange(1000)]
    else:
        max_leaf_nodes = [input_model.max_leaf_nodes, input_model.max_leaf_nodes - 2, input_model.max_leaf_nodes - 1, 
                     input_model.max_leaf_nodes + 1, input_model.max_leaf_nodes + 2, random.randrange(1000)]
        max_leaf_nodes = [i for i in max_leaf_nodes if i > 0]
    
    for l in max_leaf_nodes:
        for sam in min_samples_leaf:
            for m in max_depth:
                for c in criterion:
                    for s in splitter:
                        test_model = DecisionTreeClassifier(criterion = c, splitter = s, max_depth = m,
                                                            min_samples_leaf=sam, max_leaf_nodes = l, random_state=75)
                        score = get_ev(input_df, test_model, input_features, input_labels, odds_input)
                        if score > best_score:
                            best_score = score
                            output_model = test_model
                            print("Criterion:", c, "splitter:", s, "max_depth:", m, 
                                  "min_samples_leaf:", sam, "max_leaf_nodes:", l, best_score)        
    
    
    
    return output_model




In [34]:
def tune_RandomForestClassifier(input_model, input_features, input_df, input_labels, odds_input):
    ###############################################################################################################
    #Parameters we are going to fine-tune:
    #1. criterion ('gini', 'entropy')
    #2. max_features ('auto', 'sqrt', 'log2')
    #3. max_depth ('none', IF A NUMBER EXISTS +2, +4, -2, -4 ELSE 4 RANDOM INTS 1->100)
    #4. min_samples_leaf(n-1, n-2, 0,  n+1, n+2)
    #5. max_leaf_nodes:('none', n+1, n+2, n-1, n-2, OR 4 random numbers)
    #6. n_estimators: (n, n+1, n+2, n-1, n-2)
    ###############################################################################################################    
    output_model = input_model
    best_score = get_ev(input_df, input_model, input_features, input_labels, odds_input)
    #1. criterion ('gini', 'entropy')
    criterion = ['gini', 'entropy']
    #2. max_features ('auto', 'sqrt', 'log2')
    max_features = ['auto', 'sqrt', 'log2', None]
    #3. max_depth ('none', IF A NUMBER EXISTS +2, +4, -2, -4 ELSE 4 RANDOM INTS 1->100)
    if input_model.max_depth == None:
        max_depth = [None, random.randrange(100), random.randrange(100), random.randrange(100), random.randrange(100)]
    else:
        max_depth = [input_model.max_depth, input_model.max_depth - 2, input_model.max_depth - 1,  
                     input_model.max_depth + 1, input_model.max_depth + 2, random.randrange(100)]
        max_depth = [i for i in max_depth if i > 0]
    #4. min_samples_leaf(n-1, n-2, 0,  n+1, n+2)
    min_samples_leaf = [input_model.min_samples_leaf, input_model.min_samples_leaf - 2, input_model.min_samples_leaf - 1,
                         input_model.min_samples_leaf + 1, input_model.min_samples_leaf + 2, random.randrange(100)]
    min_samples_leaf = [i for i in min_samples_leaf if i > 0]
    
    #5. max_leaf_nodes:('none', n+1, n+2, n-1, n-2, OR 4 random numbers)
    if input_model.max_leaf_nodes == None:
        max_leaf_nodes = [None, random.randrange(1000), random.randrange(1000), random.randrange(1000), random.randrange(1000)]
    else:
        max_leaf_nodes = [input_model.max_leaf_nodes, input_model.max_leaf_nodes - 2, input_model.max_leaf_nodes - 1, 
                     input_model.max_leaf_nodes + 1, input_model.max_leaf_nodes + 2, random.randrange(1000)]
        max_leaf_nodes = [i for i in max_leaf_nodes if i > 0]
    n_estimators = [input_model.n_estimators, input_model.n_estimators - 2, input_model.n_estimators - 1,  
                 input_model.n_estimators + 1, input_model.n_estimators + 2, random.randrange(200)]
    n_estimators = [i for i in n_estimators if i > 0]
    
    
    
    for n in n_estimators:
        for ml in max_leaf_nodes:
            for ms in min_samples_leaf:
                for md in max_depth:
                    for mf in max_features:
                        for c in criterion:
                            test_model = RandomForestClassifier(n_estimators = n, max_leaf_nodes = ml, 
                                                                min_samples_leaf = ms,
                                                                max_depth = md, criterion = c, 
                                                                max_features = mf, random_state=75)
                            score = get_ev(input_df, test_model, input_features, input_labels, odds_input)
                            if score > best_score:
                                best_score = score
                                output_model = test_model
                                print()
                                print("NEW BEST SCORE")
                                print("Criterion:", c, "max_features:", mf, "max_depth:", md, "min_samples_leaf:", ms,
                                      "max_leaf_nodes:", ml, "n_estimators", n, best_score)        
                                print()
                                print()
                            else:
                                print("Criterion:", c, "max_features:", mf, "max_depth:", md, "min_samples_leaf:", ms,
                                      "max_leaf_nodes:", ml, "n_estimators", n, score)        
                            
    return output_model

In [83]:
def tune_GradientBoostingClassifier(input_model, input_features, input_df, input_labels, odds_input):
    ###############################################################################################################
    #Parameters we are going to fine-tune:
    #1. criterion ('friedman_mse', 'mse', 'mae')
    #2. loss ('deviance', 'exponential')
    #3. n_estimators (n, n+1, n-1)
    #4. learning_rate (learning_rate, learning_rate *1.1, learning_rate*.9)
    #5. min_samples_leaf: (n, n-1, n+1)
    #6. max_depth: (n, n+1, n-1)
    #7. max_features: (None, 'auto', 'sqrt', 'log2')
    #8. max_leaf_nodes: (None, n+1, n-1, OR 2 random numbers)
    #9. tol (n, n*1.1, n*.9)
    ###############################################################################################################  
    print()
    print()
    print("Starting New Run")
    print()
    print()
    output_model = input_model
    best_score = get_ev(input_df, input_model, input_features, input_labels, odds_input)
    print("Previous Best Score:", best_score)
    
    #1. criterion ('friedman_mse', 'mse', 'mae')
    criterion = ['friedman_mse', 'mse', 'mae']
    
    #2. loss ('deviance', 'exponential')
    loss = ['deviance', 'exponential']

    #3. n_estimators (n, n+1, n-1)
    n_estimators = [input_model.n_estimators, input_model.n_estimators - 1,  input_model.n_estimators + 1,
                    random.randrange(200)]
    n_estimators = [i for i in n_estimators if i > 0]    
    
    #4. learning_rate (learning_rate, learning_rate *1.1, learning_rate*.9)
    learning_rate = [input_model.learning_rate, input_model.learning_rate * 1.1, input_model.learning_rate * 0.9]
    
    #5. min_samples_leaf: (n, n-1, n+1)
    min_samples_leaf = [input_model.min_samples_leaf, input_model.min_samples_leaf - 1,
                         input_model.min_samples_leaf + 1]
    min_samples_leaf = [i for i in min_samples_leaf if i > 0]

    #6. max_depth: (n, n+1, n-1)
    if input_model.max_depth == None:
        max_depth = [None, random.randrange(100), random.randrange(100)]
    else:
        max_depth = [input_model.max_depth, input_model.max_depth - 1,  
                     input_model.max_depth + 1, random.randrange(100)]
        max_depth = [i for i in max_depth if i > 0]
        
    #7. max_features: (None, 'auto', 'sqrt', 'log2')
    max_features = ['auto', 'sqrt', 'log2', None]

    #8. max_leaf_nodes: (None, n+1, n-1, OR 2 random numbers)
    if input_model.max_leaf_nodes == None:
        max_leaf_nodes = [None, random.randrange(1000), random.randrange(1000)]
    else:
        max_leaf_nodes = [input_model.max_leaf_nodes, input_model.max_leaf_nodes - 1, input_model.max_leaf_nodes + 1, 
                          random.randrange(1000)]
        max_leaf_nodes = [i for i in max_leaf_nodes if i > 0]

    #9. tol (n, n*1.1, n*.9)
    tol = [input_model.tol, input_model.tol * 1.2, input_model.tol * .8]
            
    for t in tol:
        for ml in max_leaf_nodes:    
            for mf in max_features:
                for md in max_depth:
                    for ms in min_samples_leaf:
                        for lr in learning_rate:
                            for n in n_estimators:
                                for l in loss:
                                    for c in criterion:
                                        test_model = GradientBoostingClassifier(n_estimators = n, 
                                                                                learning_rate = lr,
                                                                                criterion = c,
                                                                                min_samples_leaf = ms,
                                                                                max_depth = md,
                                                                                loss = l, 
                                                                                max_features = mf,
                                                                                max_leaf_nodes = ml,
                                                                                tol = t,
                                                                                random_state=75)
                                        score = get_ev(input_df, test_model, input_features, input_labels, odds_input)
                                        if score > best_score:
                                            best_score = score
                                            output_model = test_model
                                            print()
                                            print("NEW BEST SCORE")
                                            print("Criterion:", c,
                                                  "n_estimators:", n,
                                                  "Loss:", l,
                                                  "Learning Rate:", lr,
                                                  "Min Samples/Leaf:", ms,
                                                  "Max Depth:", md,
                                                  "Max Features:", mf,
                                                  "Max Leaf Nodes:", ml,
                                                  "tol:", t,
                                                  "Best Score:", best_score)        
                                            print()
                                            print()
                                        else:
                                            print("Criterion:", c,
                                                  "n_estimators:", n,                          
                                                  "Loss:", l, 
                                                  "Learning Rate:", lr,
                                                  "Min Samples/Leaf:", ms,
                                                  "Max Depth:", md,
                                                  "Max Features:", mf,
                                                  "Max Leaf Nodes:", ml,
                                                  "tol:", t,
                                                  "Score:", score)        

    
    return(output_model)

In [99]:
def tune_GaussianNB(input_model, input_features, input_df, input_labels, odds_input):
    ###############################################################################################################
    #Parameters we are going to fine-tune:
    #1. var_smoothing (1e-12, 1e-11, 1e-10, 1e-9, 1e-8, 1e-7, 1e-6)
    ###############################################################################################################  
    print()
    print()
    print("Starting New Run for GaussianNB")
    print()
    print()
    output_model = input_model
    best_score = get_ev(input_df, input_model, input_features, input_labels, odds_input)
    print("Previous Best Score:", best_score)    
    
    var_smoothing = [1e-12, 1e-11, 1e-10, 1e-9, 1e-8, 1e-7, 1e-6]
    
    for v in var_smoothing:
        test_model = GaussianNB(var_smoothing = v)
        score = get_ev(input_df, test_model, input_features, input_labels, odds_input)
        if score > best_score:
            best_score = score
            output_model = test_model
            print()
            print("NEW BEST SCORE")
            print("var_smoothing:", v, 
                  "Best Score:", best_score)        
            print()
            print()
        else:
            print("var_smoothing:", v, 
                  "Score:", score)        
        
    
    return output_model
    
    

In [136]:
def tune_LinearDiscriminantAnalysis(input_model, input_features, input_df, input_labels, odds_input):
    ###############################################################################################################
    #Parameters we are going to fine-tune:
    #1. solver ('svd', 'lsqr', 'eigen')
    #2. shrinking ('auto', None)
    #3. tol (previous, previous * 1.2, previous * .8, previous * 1.1, previous * .9)
    ###############################################################################################################  
    print()
    print()
    print("Starting New Run for LinearDiscriminantAnalysis")
    print()
    print()
    output_model = input_model
    best_score = get_ev(input_df, input_model, input_features, input_labels, odds_input)
    print("Previous Best Score:", best_score)    
    
    #1. solver ('svd', 'lsqr', 'eigen')
    solver = ['svd', 'lsqr', 'eigen']
    
    #2. shrinking ('auto', None)
    shrinking = ['auto', None]

    #3. tol (previous, previous * 1.2, previous * .8, previous * 1.1, previous * .9)
    tol = [input_model.tol, input_model.tol * 1.1, input_model.tol * 1.2, input_model.tol * 0.8, input_model.tol * 0.9 ]
    
    for t in tol:
        for sh in shrinking:
            for s in solver:
                if ((s == 'svd') & (sh == 'auto')):   #Shrinkage doesn't work with svd
                    pass
                else:
                    test_model = LinearDiscriminantAnalysis(solver = s, shrinkage = sh, tol = t)
                    score = get_ev(input_df, test_model, input_features, input_labels, odds_input)
                    if score > best_score:
                        best_score = score
                        output_model = test_model
                        print()
                        print("NEW BEST SCORE")
                        print("solver:", s, 
                              "shrinking:", sh,
                              "tol:", t,
                              "Best Score:", best_score)        
                        print()
                        print()
                    else:
                        print("solver:", s, 
                              "shrinking:", sh,
                              "tol:", t,
                              "Score:", score)        
        
    
    
    return output_model

In [137]:
def tune_hyperparameters(input_model, input_features, input_df, input_labels, odds_input):
    best_model = input_model
    keep_going = True
    if isinstance(input_model, LogisticRegression):
        while(keep_going):
            pos_model = (tune_LogisticRegression(input_model, input_features, input_df, input_labels, odds_input))
            
            if str(pos_model) == str(best_model):  #Direct comparisons don't seem to work....
                keep_going = False
                output_model = best_model
            else:
                best_model = pos_model

    elif isinstance(input_model, DecisionTreeClassifier):
        while(keep_going):
            pos_model = (tune_DecisionTreeClassifier(best_model, input_features, input_df, input_labels, odds_input))
            if str(pos_model) == str(best_model):  #Direct comparisons don't seem to work....
                keep_going = False
                output_model = best_model
            else:
                best_model = pos_model            
                
    elif isinstance(input_model, RandomForestClassifier):
        while(keep_going):
            pos_model = (tune_RandomForestClassifier(best_model, input_features, input_df, input_labels, odds_input))
            if str(pos_model) == str(best_model):  #Direct comparisons don't seem to work....
                keep_going = False
                output_model = best_model
            else:
                best_model = pos_model    
                
    elif isinstance(input_model, GradientBoostingClassifier):
        while(keep_going):
            pos_model = (tune_GradientBoostingClassifier(best_model, input_features, input_df, input_labels, odds_input))
            if str(pos_model) == str(best_model):  #Direct comparisons don't seem to work....
                keep_going = False
                output_model = best_model
            else:
                best_model = pos_model                    

    elif isinstance(input_model, GaussianNB):
        while(keep_going):
            pos_model = (tune_GaussianNB(best_model, input_features, input_df, input_labels, odds_input))
            if str(pos_model) == str(best_model):  #Direct comparisons don't seem to work....
                keep_going = False
                output_model = best_model
            else:
                best_model = pos_model                    
                
    elif isinstance(input_model, LinearDiscriminantAnalysis):
        print("HII")
        while(keep_going):
            pos_model = (tune_LinearDiscriminantAnalysis(best_model, input_features, input_df, input_labels, odds_input))
            if str(pos_model) == str(best_model):  #Direct comparisons don't seem to work....
                keep_going = False
                output_model = best_model
            else:
                best_model = pos_model                    
                
        
    else:
        output_model = input_model
    return(output_model)

In [138]:
tune_hyperparameters(model_6, features_6, df_train, label_train, odds_train)

HII


Starting New Run for LinearDiscriminantAnalysis


Previous Best Score: 56.10929228817335
solver: lsqr shrinking: auto tol: 0.0001 Score: 34.47940468908792
solver: eigen shrinking: auto tol: 0.0001 Score: 34.47940468908792
solver: svd shrinking: None tol: 0.0001 Score: 56.10929228817335
solver: lsqr shrinking: None tol: 0.0001 Score: 54.63114963071928
solver: eigen shrinking: None tol: 0.0001 Score: 54.63114963071928
solver: lsqr shrinking: auto tol: 0.00011000000000000002 Score: 34.47940468908792
solver: eigen shrinking: auto tol: 0.00011000000000000002 Score: 34.47940468908792
solver: svd shrinking: None tol: 0.00011000000000000002 Score: 56.10929228817335
solver: lsqr shrinking: None tol: 0.00011000000000000002 Score: 54.63114963071928
solver: eigen shrinking: None tol: 0.00011000000000000002 Score: 54.63114963071928
solver: lsqr shrinking: auto tol: 0.00012 Score: 34.47940468908792
solver: eigen shrinking: auto tol: 0.00012 Score: 34.47940468908792
solver: svd shrinking: None 

LinearDiscriminantAnalysis(n_components=None, priors=None, shrinkage=None,
                           solver='svd', store_covariance=False, tol=0.0001)

In [101]:
tune_hyperparameters(model_5, features_5, df_train, label_train, odds_train)

HI


Starting New Run for GaussianNB


Previous Best Score: 77.61190252807359
var_smoothing: 1e-12 Score: 77.61190252807359
var_smoothing: 1e-11 Score: 77.61190252807359
var_smoothing: 1e-10 Score: 77.61190252807359
var_smoothing: 1e-09 Score: 77.61190252807359
var_smoothing: 1e-08 Score: 77.61190252807359
var_smoothing: 1e-07 Score: 77.61190252807359
var_smoothing: 1e-06 Score: 77.61190252807359


GaussianNB(priors=None, var_smoothing=1e-09)

In [85]:
new_model_4 = tune_hyperparameters(model_4, features_4, df_train, label_train, odds_train)



Starting New Run


Previous Best Score: 128.4874220169866
Criterion: friedman_mse n_estimators: 100 Loss: deviance Learning Rate: 0.1 Min Samples/Leaf: 1 Max Depth: 3 Max Features: auto Max Leaf Nodes: None tol: 0.0001 Score: 128.4874220169866
Criterion: mse n_estimators: 100 Loss: deviance Learning Rate: 0.1 Min Samples/Leaf: 1 Max Depth: 3 Max Features: auto Max Leaf Nodes: None tol: 0.0001 Score: 128.4874220169866
Criterion: mae n_estimators: 100 Loss: deviance Learning Rate: 0.1 Min Samples/Leaf: 1 Max Depth: 3 Max Features: auto Max Leaf Nodes: None tol: 0.0001 Score: 38.13059868187759
Criterion: friedman_mse n_estimators: 100 Loss: exponential Learning Rate: 0.1 Min Samples/Leaf: 1 Max Depth: 3 Max Features: auto Max Leaf Nodes: None tol: 0.0001 Score: 62.57496039912254
Criterion: mse n_estimators: 100 Loss: exponential Learning Rate: 0.1 Min Samples/Leaf: 1 Max Depth: 3 Max Features: auto Max Leaf Nodes: None tol: 0.0001 Score: 61.1347740539586
Criterion: mae n_estimators: 100

Criterion: mse n_estimators: 179 Loss: deviance Learning Rate: 0.11000000000000001 Min Samples/Leaf: 1 Max Depth: 3 Max Features: auto Max Leaf Nodes: None tol: 0.0001 Score: 112.62247950140403
Criterion: mae n_estimators: 179 Loss: deviance Learning Rate: 0.11000000000000001 Min Samples/Leaf: 1 Max Depth: 3 Max Features: auto Max Leaf Nodes: None tol: 0.0001 Score: 41.48445092366082
Criterion: friedman_mse n_estimators: 179 Loss: exponential Learning Rate: 0.11000000000000001 Min Samples/Leaf: 1 Max Depth: 3 Max Features: auto Max Leaf Nodes: None tol: 0.0001 Score: 76.62162939071803
Criterion: mse n_estimators: 179 Loss: exponential Learning Rate: 0.11000000000000001 Min Samples/Leaf: 1 Max Depth: 3 Max Features: auto Max Leaf Nodes: None tol: 0.0001 Score: 76.62162939071803
Criterion: mae n_estimators: 179 Loss: exponential Learning Rate: 0.11000000000000001 Min Samples/Leaf: 1 Max Depth: 3 Max Features: auto Max Leaf Nodes: None tol: 0.0001 Score: 40.15662732317707
Criterion: fried

Criterion: mae n_estimators: 101 Loss: deviance Learning Rate: 0.1 Min Samples/Leaf: 2 Max Depth: 3 Max Features: auto Max Leaf Nodes: None tol: 0.0001 Score: 37.5981026614933
Criterion: friedman_mse n_estimators: 101 Loss: exponential Learning Rate: 0.1 Min Samples/Leaf: 2 Max Depth: 3 Max Features: auto Max Leaf Nodes: None tol: 0.0001 Score: 47.45978166716768
Criterion: mse n_estimators: 101 Loss: exponential Learning Rate: 0.1 Min Samples/Leaf: 2 Max Depth: 3 Max Features: auto Max Leaf Nodes: None tol: 0.0001 Score: 47.45978166716768
Criterion: mae n_estimators: 101 Loss: exponential Learning Rate: 0.1 Min Samples/Leaf: 2 Max Depth: 3 Max Features: auto Max Leaf Nodes: None tol: 0.0001 Score: 34.82424259848006
Criterion: friedman_mse n_estimators: 179 Loss: deviance Learning Rate: 0.1 Min Samples/Leaf: 2 Max Depth: 3 Max Features: auto Max Leaf Nodes: None tol: 0.0001 Score: 82.07184390981197
Criterion: mse n_estimators: 179 Loss: deviance Learning Rate: 0.1 Min Samples/Leaf: 2 Ma

Criterion: friedman_mse n_estimators: 99 Loss: exponential Learning Rate: 0.09000000000000001 Min Samples/Leaf: 2 Max Depth: 3 Max Features: auto Max Leaf Nodes: None tol: 0.0001 Score: 53.902373899771234
Criterion: mse n_estimators: 99 Loss: exponential Learning Rate: 0.09000000000000001 Min Samples/Leaf: 2 Max Depth: 3 Max Features: auto Max Leaf Nodes: None tol: 0.0001 Score: 53.902373899771234
Criterion: mae n_estimators: 99 Loss: exponential Learning Rate: 0.09000000000000001 Min Samples/Leaf: 2 Max Depth: 3 Max Features: auto Max Leaf Nodes: None tol: 0.0001 Score: 34.82424259848006
Criterion: friedman_mse n_estimators: 101 Loss: deviance Learning Rate: 0.09000000000000001 Min Samples/Leaf: 2 Max Depth: 3 Max Features: auto Max Leaf Nodes: None tol: 0.0001 Score: 87.06381035259547
Criterion: mse n_estimators: 101 Loss: deviance Learning Rate: 0.09000000000000001 Min Samples/Leaf: 2 Max Depth: 3 Max Features: auto Max Leaf Nodes: None tol: 0.0001 Score: 87.06381035259547
Criterion

Criterion: mae n_estimators: 100 Loss: exponential Learning Rate: 0.11000000000000001 Min Samples/Leaf: 1 Max Depth: 2 Max Features: auto Max Leaf Nodes: None tol: 0.0001 Score: 31.191739281998004
Criterion: friedman_mse n_estimators: 99 Loss: deviance Learning Rate: 0.11000000000000001 Min Samples/Leaf: 1 Max Depth: 2 Max Features: auto Max Leaf Nodes: None tol: 0.0001 Score: 61.97621679635172
Criterion: mse n_estimators: 99 Loss: deviance Learning Rate: 0.11000000000000001 Min Samples/Leaf: 1 Max Depth: 2 Max Features: auto Max Leaf Nodes: None tol: 0.0001 Score: 61.97621679635172
Criterion: mae n_estimators: 99 Loss: deviance Learning Rate: 0.11000000000000001 Min Samples/Leaf: 1 Max Depth: 2 Max Features: auto Max Leaf Nodes: None tol: 0.0001 Score: 31.191739281998004
Criterion: friedman_mse n_estimators: 99 Loss: exponential Learning Rate: 0.11000000000000001 Min Samples/Leaf: 1 Max Depth: 2 Max Features: auto Max Leaf Nodes: None tol: 0.0001 Score: 80.09082360995332
Criterion: ms

...

Criterion: mae n_estimators: 179 Loss: deviance Learning Rate: 0.11000000000000001 Min Samples/Leaf: 2 Max Depth: 4 Max Features: None Max Leaf Nodes: 544 tol: 8e-05 Score: 66.5271485615593
Criterion: friedman_mse n_estimators: 179 Loss: exponential Learning Rate: 0.11000000000000001 Min Samples/Leaf: 2 Max Depth: 4 Max Features: None Max Leaf Nodes: 544 tol: 8e-05 Score: 41.742145041086616
Criterion: mse n_estimators: 179 Loss: exponential Learning Rate: 0.11000000000000001 Min Samples/Leaf: 2 Max Depth: 4 Max Features: None Max Leaf Nodes: 544 tol: 8e-05 Score: 26.30915883568875
Criterion: mae n_estimators: 179 Loss: exponential Learning Rate: 0.11000000000000001 Min Samples/Leaf: 2 Max Depth: 4 Max Features: None Max Leaf Nodes: 544 tol: 8e-05 Score: 49.508148011176985
Criterion: friedman_mse n_estimators: 178 Loss: deviance Learning Rate: 0.11000000000000001 Min Samples/Leaf: 2 Max Depth: 4 Max Features: None Max Leaf Nodes: 544 tol: 8e-05 Score: 51.5810938721425
Criterion: mse n_e

Criterion: mae n_estimators: 152 Loss: deviance Learning Rate: 0.09000000000000001 Min Samples/Leaf: 2 Max Depth: 4 Max Features: None Max Leaf Nodes: 544 tol: 8e-05 Score: 67.3961901962269
Criterion: friedman_mse n_estimators: 152 Loss: exponential Learning Rate: 0.09000000000000001 Min Samples/Leaf: 2 Max Depth: 4 Max Features: None Max Leaf Nodes: 544 tol: 8e-05 Score: 24.610944329185443
Criterion: mse n_estimators: 152 Loss: exponential Learning Rate: 0.09000000000000001 Min Samples/Leaf: 2 Max Depth: 4 Max Features: None Max Leaf Nodes: 544 tol: 8e-05 Score: 28.5203826768034
Criterion: mae n_estimators: 152 Loss: exponential Learning Rate: 0.09000000000000001 Min Samples/Leaf: 2 Max Depth: 4 Max Features: None Max Leaf Nodes: 544 tol: 8e-05 Score: 58.4908495481307
Criterion: friedman_mse n_estimators: 179 Loss: deviance Learning Rate: 0.1 Min Samples/Leaf: 1 Max Depth: 41 Max Features: None Max Leaf Nodes: 544 tol: 8e-05 Score: 8.306555863449558
Criterion: mse n_estimators: 179 Lo

Criterion: mse n_estimators: 180 Loss: exponential Learning Rate: 0.11000000000000001 Min Samples/Leaf: 1 Max Depth: 41 Max Features: None Max Leaf Nodes: 544 tol: 8e-05 Score: 9.884475640982666
Criterion: mae n_estimators: 180 Loss: exponential Learning Rate: 0.11000000000000001 Min Samples/Leaf: 1 Max Depth: 41 Max Features: None Max Leaf Nodes: 544 tol: 8e-05 Score: 11.413752439794806
Criterion: friedman_mse n_estimators: 152 Loss: deviance Learning Rate: 0.11000000000000001 Min Samples/Leaf: 1 Max Depth: 41 Max Features: None Max Leaf Nodes: 544 tol: 8e-05 Score: 15.628356655838585
Criterion: mse n_estimators: 152 Loss: deviance Learning Rate: 0.11000000000000001 Min Samples/Leaf: 1 Max Depth: 41 Max Features: None Max Leaf Nodes: 544 tol: 8e-05 Score: 10.599377462408961
Criterion: mae n_estimators: 152 Loss: deviance Learning Rate: 0.11000000000000001 Min Samples/Leaf: 1 Max Depth: 41 Max Features: None Max Leaf Nodes: 544 tol: 8e-05 Score: 35.37521024692827
Criterion: friedman_ms

Criterion: mae n_estimators: 178 Loss: exponential Learning Rate: 0.1 Min Samples/Leaf: 2 Max Depth: 41 Max Features: None Max Leaf Nodes: 544 tol: 8e-05 Score: 21.8874282768179
Criterion: friedman_mse n_estimators: 180 Loss: deviance Learning Rate: 0.1 Min Samples/Leaf: 2 Max Depth: 41 Max Features: None Max Leaf Nodes: 544 tol: 8e-05 Score: 16.085520442902617
Criterion: mse n_estimators: 180 Loss: deviance Learning Rate: 0.1 Min Samples/Leaf: 2 Max Depth: 41 Max Features: None Max Leaf Nodes: 544 tol: 8e-05 Score: 27.68440968597611
Criterion: mae n_estimators: 180 Loss: deviance Learning Rate: 0.1 Min Samples/Leaf: 2 Max Depth: 41 Max Features: None Max Leaf Nodes: 544 tol: 8e-05 Score: 30.43002625132944
Criterion: friedman_mse n_estimators: 180 Loss: exponential Learning Rate: 0.1 Min Samples/Leaf: 2 Max Depth: 41 Max Features: None Max Leaf Nodes: 544 tol: 8e-05 Score: 29.887556634288522
Criterion: mse n_estimators: 180 Loss: exponential Learning Rate: 0.1 Min Samples/Leaf: 2 Max D

Criterion: friedman_mse n_estimators: 178 Loss: deviance Learning Rate: 0.09000000000000001 Min Samples/Leaf: 2 Max Depth: 41 Max Features: None Max Leaf Nodes: 544 tol: 8e-05 Score: 36.8030157135092
Criterion: mse n_estimators: 178 Loss: deviance Learning Rate: 0.09000000000000001 Min Samples/Leaf: 2 Max Depth: 41 Max Features: None Max Leaf Nodes: 544 tol: 8e-05 Score: 33.2424468912384
Criterion: mae n_estimators: 178 Loss: deviance Learning Rate: 0.09000000000000001 Min Samples/Leaf: 2 Max Depth: 41 Max Features: None Max Leaf Nodes: 544 tol: 8e-05 Score: 6.005380723158497
Criterion: friedman_mse n_estimators: 178 Loss: exponential Learning Rate: 0.09000000000000001 Min Samples/Leaf: 2 Max Depth: 41 Max Features: None Max Leaf Nodes: 544 tol: 8e-05 Score: 20.894445867575904
Criterion: mse n_estimators: 178 Loss: exponential Learning Rate: 0.09000000000000001 Min Samples/Leaf: 2 Max Depth: 41 Max Features: None Max Leaf Nodes: 544 tol: 8e-05 Score: 30.198511511837413
Criterion: mae n

In [86]:
print(new_model_4)

GradientBoostingClassifier(ccp_alpha=0.0, criterion='mse', init=None,
                           learning_rate=0.1, loss='deviance', max_depth=3,
                           max_features='sqrt', max_leaf_nodes=None,
                           min_impurity_decrease=0.0, min_impurity_split=None,
                           min_samples_leaf=1, min_samples_split=2,
                           min_weight_fraction_leaf=0.0, n_estimators=179,
                           n_iter_no_change=None, presort='deprecated',
                           random_state=75, subsample=1.0, tol=0.0001,
                           validation_fraction=0.1, verbose=0,
                           warm_start=False)


In [47]:
tune_hyperparameters(model_3, features_3, df_train, label_train, odds_train)

Criterion: gini max_features: auto max_depth: None min_samples_leaf: 1 max_leaf_nodes: None n_estimators 100 141.9555746512028
Criterion: entropy max_features: auto max_depth: None min_samples_leaf: 1 max_leaf_nodes: None n_estimators 100 129.34757114859815
Criterion: gini max_features: sqrt max_depth: None min_samples_leaf: 1 max_leaf_nodes: None n_estimators 100 141.9555746512028
Criterion: entropy max_features: sqrt max_depth: None min_samples_leaf: 1 max_leaf_nodes: None n_estimators 100 129.34757114859815
Criterion: gini max_features: log2 max_depth: None min_samples_leaf: 1 max_leaf_nodes: None n_estimators 100 141.9555746512028
Criterion: entropy max_features: log2 max_depth: None min_samples_leaf: 1 max_leaf_nodes: None n_estimators 100 129.34757114859815

NEW BEST SCORE
Criterion: gini max_features: None max_depth: None min_samples_leaf: 1 max_leaf_nodes: None n_estimators 100 146.1505454262852


Criterion: entropy max_features: None max_depth: None min_samples_leaf: 1 max_lea

KeyboardInterrupt: 

In [11]:
tune_hyperparameters(model_2, features_2, df_train, label_train, odds_train)

Criterion: gini splitter: random max_depth: 13 min_samples_leaf: 1 max_leaf_nodes: 144 73.10984269006656
Criterion: entropy splitter: random max_depth: 13 min_samples_leaf: 1 max_leaf_nodes: 144 120.09023623685835


DecisionTreeClassifier(ccp_alpha=0.0, class_weight=None, criterion='entropy',
                       max_depth=13, max_features=None, max_leaf_nodes=144,
                       min_impurity_decrease=0.0, min_impurity_split=None,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, presort='deprecated',
                       random_state=75, splitter='random')

In [46]:
tune_hyperparameters(model_1, features_1, df_train, label_train, odds_train)

l2 newton-cg 0.0001 53.06760226712672
none newton-cg 0.0001 55.4021265248508
none saga 0.0001 55.607690050410156


LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
                   intercept_scaling=1, l1_ratio=None, max_iter=10000,
                   multi_class='auto', n_jobs=None, penalty='none',
                   random_state=75, solver='saga', tol=0.0001, verbose=0,
                   warm_start=False)